<a href="https://colab.research.google.com/github/rishis123/HealthTrendsCode/blob/main/final_hospitalization_model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

import statsmodels.api as sm
import statsmodels.formula.api as smf
import matplotlib.pyplot as plt

from statsmodels.stats.diagnostic import het_breuschpagan
from statsmodels.tsa.stattools import adfuller
from patsy import dmatrices
import itertools


from statsmodels.formula.api import glm

import matplotlib.pyplot as plt

from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from math import sqrt




In [ ]:
file_path = '/content/HospitalNYS.csv'
df_hospital = pd.read_csv(file_path)
df_hospital = df_hospital.rename(columns={"As of Date": "ds", "Facility County": "County"})
print(df_hospital.tail())
print(df_hospital.shape)


                ds    County  Patients Currently Hospitalized  \
259804  03/26/2020     YATES                                0   
259805  03/26/2020  SCHUYLER                                0   
259806  03/26/2020   STEUBEN                                0   
259807  03/26/2020   STEUBEN                                0   
259808  03/26/2020  ONONDAGA                                6   

        Patients Admitted Due to COVID  Patients Admitted Not Due to COVID  
259804                               0                                   0  
259805                               0                                   0  
259806                               0                                   0  
259807                               0                                   0  
259808                               0                                   0  
(259809, 5)


In [ ]:
df_hospital['ds'] = pd.to_datetime(df_hospital['ds'], format='%m/%d/%Y') #convert to datetime fromat

df_hospital = df_hospital.groupby(['ds', 'County']).sum().reset_index() #We add all other values for columns that share values
df_hospital = df_hospital.drop_duplicates(subset=['ds', 'County']) #drop duplicates
df_hospital = df_hospital.sort_values(by=['ds']).reset_index(drop=True)
print(df_hospital.head())
print(df_hospital.shape)


          ds    County  Patients Currently Hospitalized  \
0 2020-03-26    ALBANY                               22   
1 2020-03-26  ONONDAGA                               19   
2 2020-03-26   ONTARIO                                3   
3 2020-03-26    ORANGE                               62   
4 2020-03-26   ORLEANS                                1   

   Patients Admitted Due to COVID  Patients Admitted Not Due to COVID  
0                               0                                   0  
1                               0                                   0  
2                               0                                   0  
3                               0                                   0  
4                               0                                   0  
(74556, 5)


In [ ]:
counties = df_hospital['County'].unique()
print(counties)

['ALBANY' 'ONONDAGA' 'ONTARIO' 'ORANGE' 'ORLEANS' 'OSWEGO' 'OTSEGO'
 'PUTNAM' 'QUEENS' 'RENSSELAER' 'RICHMOND' 'ROCKLAND' 'SCHENECTADY'
 'SCHOHARIE' 'SCHUYLER' 'ST. LAWRENCE' 'STEUBEN' 'SUFFOLK' 'SULLIVAN'
 'TOMPKINS' 'ULSTER' 'WARREN' 'WAYNE' 'WESTCHESTER' 'WYOMING' 'YATES'
 'ONEIDA' 'NIAGARA' 'SARATOGA' 'NASSAU' 'NEW YORK' 'BRONX' 'BROOME'
 'CATTARAUGUS' 'CAYUGA' 'CHAUTAUQUA' 'CHEMUNG' 'CHENANGO' 'CLINTON'
 'COLUMBIA' 'CORTLAND' 'DELAWARE' 'DUTCHESS' 'ALLEGANY' 'MONTGOMERY'
 'ERIE' 'MONROE' 'MADISON' 'LIVINGSTON' 'KINGS' 'LEWIS' 'HERKIMER'
 'GENESEE' 'FULTON' 'FRANKLIN' 'ESSEX' 'JEFFERSON']


In [ ]:


# Function to find best ARIMA parameters for a given time series
def find_best_arima_parameters(time_series):
    # Define the range of p and q values (d is fixed at 1)
    p = q = range(0, 5)
    pdq = list(itertools.product(p, [1], q))

    # Initialize variables for best model selection
    best_aic = float('inf')  # Set initial best AIC to infinity (lower the better)
    best_param = None # Best possible (p, d, q) combo, but d at 1.

    # Iterate through all possible combinations of p and q
    for param in pdq:
        try:
            print(f"Testing ARIMA parameters: {param}")  # Print current parameters being tested
            # Fit ARIMA model
            model_arima = sm.tsa.ARIMA(time_series, order=param)
            model_arima_fit = model_arima.fit()

            # Update best model if current model has lower AIC
            if model_arima_fit.aic < best_aic:
                best_aic = model_arima_fit.aic
                best_param = param

        except Exception as e:
            continue

    # Return the best parameters found
    return best_param, best_aic

In [ ]:
results = [] #optimal p, d, q values for arima
for county in counties:
    print('curr_county: ' + county)
    county_data = df_hospital[df_hospital['County'] == county]
    hospitalized_count = county_data['Patients Currently Hospitalized']

    # First order difference to ensure stationarity (d = 1)
    hospitalized_count_diff = hospitalized_count.diff().dropna()

    # Find best ARIMA parameters for the county
    best_param, best_aic = find_best_arima_parameters(hospitalized_count_diff)

    # Append the results to the List
    results.append({'County': county, 'Best Param': best_param, 'Best AIC': best_aic})

Testing ARIMA parameters: (0, 1, 0)
Testing ARIMA parameters: (0, 1, 1)


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dat

Testing ARIMA parameters: (0, 1, 2)


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


Testing ARIMA parameters: (0, 1, 3)


...

/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


Testing ARIMA parameters: (4, 1, 3)


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


Testing ARIMA parameters: (4, 1, 4)


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


In [ ]:
print(results)

[{'County': 'ALBANY', 'Best Param': (4, 1, 3), 'Best AIC': 7842.942421530616}, {'County': 'ONONDAGA', 'Best Param': (3, 1, 1), 'Best AIC': 8365.764207954846}, {'County': 'ONTARIO', 'Best Param': (4, 1, 2), 'Best AIC': 6224.250127895495}, {'County': 'ORANGE', 'Best Param': (4, 1, 4), 'Best AIC': 8028.65467956714}, {'County': 'ORLEANS', 'Best Param': (1, 1, 2), 'Best AIC': 1951.8062358656907}, {'County': 'OSWEGO', 'Best Param': (1, 1, 3), 'Best AIC': 4590.763902221681}, {'County': 'OTSEGO', 'Best Param': (1, 1, 4), 'Best AIC': 5176.562488714131}, {'County': 'PUTNAM', 'Best Param': (4, 1, 4), 'Best AIC': 4655.557865336063}, {'County': 'QUEENS', 'Best Param': (4, 1, 4), 'Best AIC': 11033.661203244319}, {'County': 'RENSSELAER', 'Best Param': (4, 1, 4), 'Best AIC': 5479.558372470752}, {'County': 'RICHMOND', 'Best Param': (4, 1, 4), 'Best AIC': 8839.025808432241}, {'County': 'ROCKLAND', 'Best Param': (3, 1, 4), 'Best AIC': 8001.472565172795}, {'County': 'SCHENECTADY', 'Best Param': (3, 1, 4),

In [ ]:
results = [{'County': 'ALBANY', 'Best Param': (4, 1, 3), 'Best AIC': 7842.942421530616}, {'County': 'ONONDAGA', 'Best Param': (3, 1, 1), 'Best AIC': 8365.764207954846}, {'County': 'ONTARIO', 'Best Param': (4, 1, 2), 'Best AIC': 6224.250127895495}, {'County': 'ORANGE', 'Best Param': (4, 1, 4), 'Best AIC': 8028.65467956714}, {'County': 'ORLEANS', 'Best Param': (1, 1, 2), 'Best AIC': 1951.8062358656907}, {'County': 'OSWEGO', 'Best Param': (1, 1, 3), 'Best AIC': 4590.763902221681}, {'County': 'OTSEGO', 'Best Param': (1, 1, 4), 'Best AIC': 5176.562488714131}, {'County': 'PUTNAM', 'Best Param': (4, 1, 4), 'Best AIC': 4655.557865336063}, {'County': 'QUEENS', 'Best Param': (4, 1, 4), 'Best AIC': 11033.661203244319}, {'County': 'RENSSELAER', 'Best Param': (4, 1, 4), 'Best AIC': 5479.558372470752}, {'County': 'RICHMOND', 'Best Param': (4, 1, 4), 'Best AIC': 8839.025808432241}, {'County': 'ROCKLAND', 'Best Param': (3, 1, 4), 'Best AIC': 8001.472565172795}, {'County': 'SCHENECTADY', 'Best Param': (3, 1, 4), 'Best AIC': 5864.544838709879}, {'County': 'SCHOHARIE', 'Best Param': (4, 1, 4), 'Best AIC': 2530.312157124102}, {'County': 'SCHUYLER', 'Best Param': (2, 1, 3), 'Best AIC': 1263.3346486674777}, {'County': 'ST. LAWRENCE', 'Best Param': (3, 1, 1), 'Best AIC': 5513.250346355006}, {'County': 'STEUBEN', 'Best Param': (3, 1, 2), 'Best AIC': 5071.2881143475615}, {'County': 'SUFFOLK', 'Best Param': (4, 1, 3), 'Best AIC': 10667.26771653881}, {'County': 'SULLIVAN', 'Best Param': (2, 1, 1), 'Best AIC': 4674.6489749976645}, {'County': 'TOMPKINS', 'Best Param': (4, 1, 1), 'Best AIC': 5048.08007285358}, {'County': 'ULSTER', 'Best Param': (4, 1, 4), 'Best AIC': 5318.131079797895}, {'County': 'WARREN', 'Best Param': (4, 1, 3), 'Best AIC': 5484.76490125686}, {'County': 'WAYNE', 'Best Param': (2, 1, 3), 'Best AIC': 5036.269185779647}, {'County': 'WESTCHESTER', 'Best Param': (4, 1, 4), 'Best AIC': 9596.978771308228}, {'County': 'WYOMING', 'Best Param': (4, 1, 1), 'Best AIC': 3811.118010159722}, {'County': 'YATES', 'Best Param': (1, 1, 3), 'Best AIC': 1956.8790314216567}, {'County': 'ONEIDA', 'Best Param': (2, 1, 3), 'Best AIC': 7115.241243291324}, {'County': 'NIAGARA', 'Best Param': (4, 1, 4), 'Best AIC': 5315.163707811164}, {'County': 'SARATOGA', 'Best Param': (0, 1, 1), 'Best AIC': 5733.616519737066}, {'County': 'NASSAU', 'Best Param': (4, 1, 4), 'Best AIC': 11098.452613994803}, {'County': 'NEW YORK', 'Best Param': (4, 1, 3), 'Best AIC': 11700.371151105312}, {'County': 'BRONX', 'Best Param': (4, 1, 4), 'Best AIC': 11124.540053094404}, {'County': 'BROOME', 'Best Param': (3, 1, 4), 'Best AIC': 7425.557786508776}, {'County': 'CATTARAUGUS', 'Best Param': (4, 1, 1), 'Best AIC': 5429.870929959091}, {'County': 'CAYUGA', 'Best Param': (3, 1, 4), 'Best AIC': 4790.142108547316}, {'County': 'CHAUTAUQUA', 'Best Param': (2, 1, 3), 'Best AIC': 5432.476417508968}, {'County': 'CHEMUNG', 'Best Param': (4, 1, 1), 'Best AIC': 5198.083946904064}, {'County': 'CHENANGO', 'Best Param': (1, 1, 4), 'Best AIC': 3161.907827081321}, {'County': 'CLINTON', 'Best Param': (0, 1, 4), 'Best AIC': 5802.399068741714}, {'County': 'COLUMBIA', 'Best Param': (2, 1, 3), 'Best AIC': 5037.76635325109}, {'County': 'CORTLAND', 'Best Param': (4, 1, 3), 'Best AIC': 4327.148986629214}, {'County': 'DELAWARE', 'Best Param': (4, 1, 3), 'Best AIC': 2927.898266252324}, {'County': 'DUTCHESS', 'Best Param': (4, 1, 4), 'Best AIC': 7408.831056207489}, {'County': 'ALLEGANY', 'Best Param': (3, 1, 4), 'Best AIC': 4010.862495453342}, {'County': 'MONTGOMERY', 'Best Param': (0, 1, 4), 'Best AIC': 4679.198964377754}, {'County': 'ERIE', 'Best Param': (2, 1, 3), 'Best AIC': 9195.884348031168}, {'County': 'MONROE', 'Best Param': (2, 1, 4), 'Best AIC': 9387.414300854714}, {'County': 'MADISON', 'Best Param': (2, 1, 4), 'Best AIC': 4619.565598359275}, {'County': 'LIVINGSTON', 'Best Param': (3, 1, 4), 'Best AIC': 4287.303216752993}, {'County': 'KINGS', 'Best Param': (4, 1, 3), 'Best AIC': 11347.160651146232}, {'County': 'LEWIS', 'Best Param': (4, 1, 4), 'Best AIC': 3698.0544646485087}, {'County': 'HERKIMER', 'Best Param': (4, 1, 4), 'Best AIC': 2838.36684371942}, {'County': 'GENESEE', 'Best Param': (0, 1, 4), 'Best AIC': 4978.269050397351}, {'County': 'FULTON', 'Best Param': (0, 1, 4), 'Best AIC': 4115.56639121115}, {'County': 'FRANKLIN', 'Best Param': (2, 1, 3), 'Best AIC': 4114.783572671956}, {'County': 'ESSEX', 'Best Param': (4, 1, 2), 'Best AIC': 2330.5055232160717}, {'County': 'JEFFERSON', 'Best Param': (0, 1, 3), 'Best AIC': 5463.681874244991}]


Modifying this previous code to return data in the form of a table for every county. The table should contain predictions for some time after the end of the data given, and train on past data. For example, trains on past week to predict next week -- does this for all the known data to gain further accuracy, and end result is a row with the prediction for 1 week in the future for that county, along with the R^2 and MAE of all the previous predictions.

Replicating the same thing for 1 week up to 6 weeks, and for each of the counties.

In [ ]:
# Initialize a DataFrame to store metrics
metrics_df = pd.DataFrame(columns=['County', 'Weeks Ahead', 'MAE', 'R²'])

# Get the first county in the results list
county_info = results[0]
county = county_info['County']
best_param = county_info['Best Param']  # Get p, d, q for the current county

county_data = df_hospital[df_hospital['County'] == county].copy()
# county_data = county_data[county_data['ds'] >= '2022-01-01']  # Skip first 0-only counts
county_data = county_data.sort_values('ds')  # Ensure data is sorted by date

for weeks_ahead in range(1, 7):  # From 1 week ahead to 6 weeks ahead
    print(f"PREDICTING {weeks_ahead} WEEK(S) AHEAD")
    # Initialize a DataFrame to store forecasts
    all_forecasts = pd.DataFrame(columns=['ds', 'forecast'])

    # Starting from the second week, to have sufficient data for the first prediction.
    start_date = county_data['ds'].min() + pd.Timedelta(days=7)
    end_date = county_data['ds'].max()
    current_date = start_date

    while current_date <= end_date:
        print(f"Current date: {current_date} and End Date: {end_date}")
        # Prepare data up to the current date for fitting the ARIMA model
        ts_data = county_data[county_data['ds'] <= current_date]['Patients Currently Hospitalized']

        # Fit the ARIMA model
        model = sm.tsa.ARIMA(ts_data, order=best_param)
        model_fit = model.fit()

        # Forecast weeks_ahead weeks ahead
        forecast_steps = weeks_ahead * 7
        forecast = model_fit.forecast(steps=forecast_steps)
        forecast_index = pd.date_range(start=current_date, periods=forecast_steps, freq='D')

        # Store the forecast
        forecast_df = pd.DataFrame({
            'ds': forecast_index,
            'forecast': forecast  # Value of forecast
        })

        all_forecasts = pd.concat([all_forecasts, forecast_df], ignore_index=True)

        # Move to the next week
        current_date += pd.Timedelta(days=7)

    # Merge the forecast with actual data for comparison
    actual_data = county_data[['ds', 'Patients Currently Hospitalized']]
    merged_df = pd.merge(all_forecasts, actual_data, on='ds')

    # Calculate MAE and R²
    mae = mean_absolute_error(merged_df['Patients Currently Hospitalized'], merged_df['forecast'])
    r2 = r2_score(merged_df['Patients Currently Hospitalized'], merged_df['forecast'])

    # Create a new row for the metrics
    new_row = {
        'County': county,
        'Weeks Ahead': weeks_ahead,
        'MAE': mae,
        'R²': r2
    }

    # Append the new row to the metrics DataFrame
    metrics_df = pd.concat([metrics_df, pd.DataFrame([new_row])], ignore_index=True)


PREDICTING 1 WEEK(S) AHEAD
Current date: 2020-04-02 00:00:00 and End Date: 2024-06-24 00:00:00


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Lik

Current date: 2020-04-09 00:00:00 and End Date: 2024-06-24 00:00:00


/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473

Current date: 2020-04-16 00:00:00 and End Date: 2024-06-24 00:00:00


...

/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An u

Current date: 2024-06-13 00:00:00 and End Date: 2024-06-24 00:00:00


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An u

Current date: 2024-06-20 00:00:00 and End Date: 2024-06-24 00:00:00


/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(


In [ ]:
print(metrics_df)

NameError: name 'metrics_df' is not defined

:   County Weeks Ahead        MAE        R²
0  ALBANY           1   6.077888  0.971347
1  ALBANY           2   9.782495  0.916370
2  ALBANY           3  13.111484  0.828817
3  ALBANY           4  16.361228  0.718408
4  ALBANY           5  19.467630  0.592609
5  ALBANY           6  22.440625  0.454958

Things to research:

- What did other papers on wastewater do?
  - https://github.com/CDCgov/wastewater-informed-covid-forecasting?tab=readme-ov-file#installing-and-running-code
  - The CDC did what I did with national data on wastewater and hospitalization including the full data-sourcing and cleaning pipeline.
  #This is useful to integrate with whatever data we get, as if we find something also relevant, then we can build the ensemble model.
  - Build upon EpiNow2 statistical model

- Possibility of Switching to non time-series data (if such data was available):

  - Pros:
    - Better documented
    - More easily usable/personalizable(?) recommendations
  - Cons:
    - https://www.akkio.com/applications/employee-absenteeism -> competitor

- Switching direction?

  - https://www.google.com/url?sa=t&source=web&rct=j&opi=89978449&url=https://www.ncbi.nlm.nih.gov/pmc/articles/PMC9972778/&ved=2ahUKEwir4vmXtamHAxXyFFkFHRg9A1gQFnoECBQQAQ&usg=AOvVaw0CO27iLqi7fKFymd4K3HHY
  - Large concern was predicting absenteeism among union employees of a hospital, but problem is data availability. Conversely, predicting absenteeism among patients allows for more effective employee management.

  - https://health.data.ny.gov/

Points about deployment

- Are all these proxy data sources, and NY as subset of national, viable for a production usecase?

- Currently, model is just ARIMA -- should I focus on ensembles to increase accuracy. If so, what else should be used?

- Are these models useful? They will always yield same result, because data-source is static (not being queried during runtime).

With NYS dataset example, can generate data-based survey for employees

- E.g., Childhood lead testing (for children of employees). If significant correlation exists with hospitalization, then asking region of chlid's birth/early life (to consider for lags?) may be useful for absenteeism function.

#MODEL DEPLOYMENT PIPELINE -- in general

1) Query Data Real-Time, sort into dfs with desired columns

2) Sort by time, organize by county(?)

3) Find optimal ARIMA parameters (if using) with AIC logic above. Consider SARIMAX (with exogeneous variables/predictors)

4) Train all models. For multiple predictors (if assessing each metrics' value over time) -> then:

LSTM (Long Short-Term Memory) Networks: Useful for capturing long-term dependencies in time-series data.

XGBoost or Random Forests: Effective for handling complex interactions between features in a tabular format.

VAR (Vector AutoRegression): Useful for multivariate time series data.


In [ ]:
#Querying NYS hospitalization dataset -- for trying SIMLR
import requests
import pandas as pd

# API endpoint
url = "https://health.data.ny.gov/resource/jw46-jpb7.json"

# Request data
response = requests.get(url)

# Convert to DataFrame
data = pd.DataFrame(response.json())


In [ ]:
# Display the data
print(data.columns)
print(data.shape)

Index(['as_of_date', 'facility_pfi', 'facility_name', 'doh_region',
       'facility_county', 'facility_network', 'ny_forward_region',
       'patients_currently', 'patients_admitted_due_to_covid',
       'patients_admitted_not_due_to_covid', 'patients_newly_admitted',
       'patients_positive_after', 'patients_discharged',
       'patients_currently_in_icu', 'patients_currently_icu',
       'patients_expired', 'cumulative_covid_19_discharges',
       'cumulative_covid_19_fatalities', 'total_staffed_beds',
       'total_staffed_beds_currently', 'total_staffed_icu_beds',
       'total_staffed_icu_beds_2', 'total_staffed_acute_care',
       'total_staffed_acute_care_1', 'total_staffed_icu_beds_1',
       'total_staffed_icu_beds_3', 'total_new_admissions_reported',
       'patients_age_lt1', 'patients_age_1_4', 'patients_age_5_19',
       'patients_age_20_44', 'patients_age_45_54', 'patients_age_55_64',
       'patients_age_65_74', 'patients_age_75_84', 'patients_age_greater_85',
       

#NOTE: NOT LOOKING AT HOSPITALIZATION

In [ ]:
#SAME PREDICTION 1 WEEK AHEAD, BUT WITH ARIMA
import os
from statsmodels.tsa.arima.model import ARIMA

metrics = []
save_dir = '/content/drive/MyDrive/final_arima_forecasts'
os.makedirs(save_dir, exist_ok=True)

#Better iterating through results than through the counties for easy access from list of dictionaries
for county_info in results:
    county = county_info['County']
    best_param = county_info['Best Param']    # Get p, d, q for the current county

    county_data = df_hospital[df_hospital['County'] == county].copy()
    county_data = county_data[county_data['ds'] >= '2022-01-01'] #Skip first 0-only counts
    county_data = county_data.sort_values('ds')  # Ensure data is sorted by date

    # Initialize a dataframe to store forecasts
    all_forecasts = pd.DataFrame(columns=['ds', 'forecast', 'lower_bound', 'upper_bound'])

    # Starting from the second week, to have sufficient data for first prediction.
    start_date = county_data['ds'].min() + pd.Timedelta(days=7)
    end_date = county_data['ds'].max()
    current_date = start_date

    while current_date <= end_date:
        # Prepare data up to the current date for fitting the ARIMA model
        ts_data = county_data[county_data['ds'] <= current_date]['Patients Admitted Due to COVID']

        # Fit the ARIMA model
        model = ARIMA(ts_data, order=best_param) #best_param from previous AIC check
        model_fit = model.fit()

        # Forecast one week ahead
        forecast_steps = 7
        forecast = model_fit.forecast(steps=forecast_steps)
        forecast_index = pd.date_range(start=current_date, periods=forecast_steps, freq='D')

        # Store the forecast, problem with cache in confidence interval?
        forecast_df = pd.DataFrame({
            'ds': forecast_index,
            'forecast': forecast, #Value of forecast
        })

        all_forecasts = pd.concat([all_forecasts, forecast_df], ignore_index=True) #Add next week's forecast to df of all forecasts

        # Move to the next week
        current_date += pd.Timedelta(days=7)

    # Merge the forecast with actual data for comparison
    actual_data = county_data[['ds', 'Patients Admitted Due to COVID']]
    merged_df = pd.merge(all_forecasts, actual_data, on='ds')

    # Calculate MAE and R^2
    mae = mean_absolute_error(merged_df['Patients Admitted Due to COVID'], merged_df['forecast'])
    r2 = r2_score(merged_df['Patients Admitted Due to COVID'], merged_df['forecast'])

    # Plotting the actual data
    plt.figure(figsize=(10, 6))
    plt.plot(county_data['ds'], county_data['Patients Admitted Due to COVID'], label='Actual')

    # Plotting the forecast, and shade confidence intervals around prediction.
    plt.plot(all_forecasts['ds'], all_forecasts['forecast'], label='Forecast')

    plt.title(f'Forecast for {county}')
    plt.xlabel('Date')
    plt.ylabel('Patients Admitted Due to COVID')
    plt.legend(title=f'MAE: {mae:.2f}, R²: {r2:.2f}') #Add the statistics to the legen

    # Save the plot
    plot_path = os.path.join(save_dir, f'forecast_{county}.png')
    plt.savefig(plot_path)
    plt.close()